# Imports

Przed rozpoczęciem pracy potrzebny jest import wszystkich bibliotek, z których będziemy korzystać

- **os** odpowiedzialny za przetwarzanie plików systemu
- **cv2** używana jest do przetwarzania obrazów oraz wideo
- **numpy** ułatwia wykonywanie obliczeń
- **pytesseract** narzędzie do rozpoznawania tekstu w obrazach (OCR)
- **plotly.express**: biblioteka do tworzenia interaktywnych wykresów, ułatwia wizualizację danych.
- **xml.etree.ElementTree**: moduł do parsowania i tworzenia dokumentów XML, używany do pracy z danymi zapisanymi w formacie XML.
- **matplotlib.pyplot**: moduł do tworzenia wykresów, używany do wizualizacji danych w formie statycznych wykresów.
- **glob**: pozwala na znajdowanie wszystkich ścieżek do plików pasujących do określonego wzorca.
- **sklearn.model_selection**: moduł zawierający funkcje do podziału danych na zbiory treningowe i testowe, niezbędne do walidacji modeli.

- **tensorflow** zawiera metody potrzebne do tworzenie modeli uczenia maszynowego
    - **tensorflow.keras.models**: moduł zawierający funkcje do budowy i kompilacji modeli, wspiera tworzenie modeli uczenia głębokiego.
    - **tensorflow.keras.callbacks**: zawiera klasy i funkcje do obsługi wywołań zwrotnych podczas treningu modeli, takie jak TensorBoard do monitorowania procesu treningu.
    - **tensorflow.keras.applications**: zawiera predefiniowane architektury modeli, takie jak InceptionResNetV2, które można używać jako podstawę do transfer learningu.
    - **tensorflow.keras.layers**: moduł zawierający różne warstwy, które można dodawać do modeli, takie jak Dense, Dropout, Flatten, oraz Input.
    - **tensorflow.keras.preprocessing.image**: moduł do przetwarzania obrazów, zawiera funkcje takie jak load_img i img_to_array do wczytywania i konwersji obrazów na tablice numeryczne.


In [10]:
import os
import cv2
import numpy as np
import pandas as pd
import tensorflow as tf
import pytesseract as pt
import plotly.express as px
import xml.etree.ElementTree as xet
import matplotlib.pyplot as plt

from glob import glob
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import TensorBoard
from sklearn.model_selection import train_test_split
from tensorflow.keras.applications import InceptionResNetV2
from tensorflow.keras.layers import Dense, Dropout, Flatten, Input
from tensorflow.keras.preprocessing.image import load_img, img_to_array
print("import succesfull")

import succesfull


Biblioteka `pytesseract` wymaga dodania ścieżki do pliku wykonywalnego Tesseract, aby mogła poprawnie działać

In [3]:
pt.pytesseract.tesseract_cmd = r'C:\Program Files\Tesseract-OCR\tesseract.exe'

# Loading Data
Wczytujemy annotacje zdjęć do Dataframe. Każdemu zdjęciu odpowiada plik .xml o tej samej nazwie. Przykład pliku .xml:

```
<annotation>
	<folder></folder>
	<filename>N1.jpeg</filename>
	<path>/Users/asik/Desktop/ANPR/images/N1.jpeg</path>
	<source>
		<database>Unknown</database>
	</source>
	<size>
		<width>1920</width>
		<height>1080</height>
		<depth>3</depth>
	</size>
	<segmented>0</segmented>
	<object>
		<name>number_plate</name>
		<pose>Unspecified</pose>
		<truncated>0</truncated>
		<difficult>0</difficult>
		<bndbox>
			<xmin>1093</xmin>
			<ymin>645</ymin>
			<xmax>1396</xmax>
			<ymax>727</ymax>
		</bndbox>
	</object>
</annotation>
```
Annotacje zostały wcześniej dodane przez użytkownika Kaggle.

In [4]:
path = glob('kaggle_dataset001/images/*.xml')
labels_dict = dict(filepath=[],xmin=[],xmax=[],ymin=[],ymax=[])
for filename in path:
    
    info = xet.parse(filename)
    root = info.getroot()
    member_object = root.find('object')
    labels_info = member_object.find('bndbox')
    xmin = int(labels_info.find('xmin').text)
    xmax = int(labels_info.find('xmax').text)
    ymin = int(labels_info.find('ymin').text)
    ymax = int(labels_info.find('ymax').text)

    labels_dict['filepath'].append(filename)
    labels_dict['xmin'].append(xmin)
    labels_dict['xmax'].append(xmax)
    labels_dict['ymin'].append(ymin)
    labels_dict['ymax'].append(ymax)

Nasz dataset składa się z następujących atrybutów:

| Atrybut | Opis |
| --------- | ---- |
| filepath | ścieżka do pliku annotacji |
| xmin | współrzędna x bliżej początku współrzędnych |
| xmax | współrzędna x bliżej końca współrzędnych |
| ymin | współrzędna y bliżej początku współrzędnych |
| ymax | współrzędna y bliżej końca współrzędnych |

Atrybuty *xmin*, *xmax*, *ymin*, *ymax* razem tworzą **bounding box**, który określa lokalizację obiektu na obrazie

In [5]:
df = pd.DataFrame(labels_dict)
df.to_csv('labels.csv',index=False)
df.head()

filepath  xmin  xmax  ymin  ymax
0    kaggle_dataset001/images\N1.xml  1093  1396   645   727
1  kaggle_dataset001/images\N100.xml   134   301   312   350
2  kaggle_dataset001/images\N101.xml    31   139   128   161
3  kaggle_dataset001/images\N102.xml   164   316   216   243
4  kaggle_dataset001/images\N103.xml   813  1067   665   724

Zmieniamy ścieżki w taki sposób, aby wskazywały na zdjęcie.

In [6]:
filename = df['filepath'][0]
def getFilename(filename):
    filename_image = xet.parse(filename).getroot().find('filename').text
    filepath_image = os.path.join('kaggle_dataset001/images/',filename_image)
    return filepath_image
getFilename(filename)

'kaggle_dataset001/images/N1.jpeg'

In [7]:
image_path = list(df['filepath'].apply(getFilename))
image_path[:10]

['kaggle_dataset001/images/N1.jpeg',
 'kaggle_dataset001/images/N100.jpeg',
 'kaggle_dataset001/images/N101.jpeg',
 'kaggle_dataset001/images/N102.jpeg',
 'kaggle_dataset001/images/N103.jpeg',
 'kaggle_dataset001/images/N104.jpeg',
 'kaggle_dataset001/images/N105.jpeg',
 'kaggle_dataset001/images/N106.jpeg',
 'kaggle_dataset001/images/N107.jpeg',
 'kaggle_dataset001/images/N108.jpeg']

# Data Veryfication
Sprawdzamy na przykładzie zdjęcia *N100.jpeg* czy wartości faktycznie odpowiadają położeniu tablicy rejestracyjnej.

In [12]:
file_path = image_path[1] #path of our image N100.jpeg
img = cv2.imread(file_path) #read the image
# x0=134, x1=301, y0=312, y1=350 
img = plt.imread(file_path) #Read the image
fig = px.imshow(img)
fig.update_layout(width=600, height=500, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='N100.jpeg with bounding box')
fig.add_shape(type='rect',x0=134, x1=301, y0=312, y1=350, xref='x', yref='y',line_color='cyan')

# Data processing

Przy użyciu OpenCV konwertujemy obrazy w tablice 244 x 244, co jest standardowym rozmiarem dla przed trenowanych modeli.

In [21]:
#Targeting all our values in array selecting all columns
labels = df.iloc[:,1:].values
data = []
output = []
for ind in range(len(image_path)):
    image = image_path[ind]
    img_arr = cv2.imread(image)
    h,w,d = img_arr.shape
    # Prepprocesing
    load_image = load_img(image,target_size=(224,224))
    load_image_arr = img_to_array(load_image)
    norm_load_image_arr = load_image_arr/255.0 # Normalization
    # Normalization to labels
    xmin,xmax,ymin,ymax = labels[ind]
    nxmin,nxmax = xmin/w,xmax/w
    nymin,nymax = ymin/h,ymax/h
    label_norm = (nxmin,nxmax,nymin,nymax) # Normalized output
    # Append
    data.append(norm_load_image_arr)
    output.append(label_norm)

konwertujemy listy na **Numpy.array**

In [22]:
# Convert data to array
X = np.array(data,dtype=np.float32)
y = np.array(output,dtype=np.float32)

Dzielimy cały zbiór na zbiory testowe i treningowe.

In [23]:
# Split the data into training and testing set using sklearn.
x_train,x_test,y_train,y_test = train_test_split(X,y,train_size=0.8,random_state=0)
x_train.shape,x_test.shape,y_train.shape,y_test.shape

((180, 224, 224, 3), (45, 224, 224, 3), (180, 4), (45, 4))

# Model Building
#TODO

In [24]:
inception_resnet = InceptionResNetV2(weights="imagenet",include_top=False, input_tensor=Input(shape=(224,224,3)))
# ---------------------
headmodel = inception_resnet.output
headmodel = Flatten()(headmodel)
headmodel = Dense(500,activation="relu")(headmodel)
headmodel = Dense(250,activation="relu")(headmodel)
headmodel = Dense(4,activation='sigmoid')(headmodel)


# ---------- model
model = Model(inputs=inception_resnet.input,outputs=headmodel)

Kompilujemy model.

Optymalizator Adam (Adaptive Moment Estimation), użyty w tym modelu, jest zaawansowanym algorytmem optymalizacji używanym w treningu modeli maszynowych. Charakteryzuje się adaptacyjnym tempem uczenia, wykorzystaniem momentu i średnią ruchomą kwadratu gradientu. Jest to dosyć powszechnie stosowany model ze względu na swoją skuteczność, uniwersalność i łatwość użycia.

#TODO

In [ ]:
# Complie model
model.compile(loss='mse',optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4))

# Training and save
Trenujemy model na wcześniej przygotowanych danych, ustawiamy parametry:
- *batch_size=10*
- *epochs=180*
#TODO callbacks

In [27]:
tfb = TensorBoard('object_detection')
history = model.fit(x=x_train,y=y_train,batch_size=10,epochs=180,
                    validation_data=(x_test,y_test),callbacks=[tfb])

Epoch 1/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 147s 3s/step - loss: 0.0658 - val_loss: 0.0679
Epoch 2/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 45s 2s/step - loss: 0.0180 - val_loss: 0.0155
Epoch 3/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 46s 3s/step - loss: 0.0101 - val_loss: 0.0250
Epoch 4/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 45s 2s/step - loss: 0.0065 - val_loss: 0.0189
Epoch 5/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 43s 2s/step - loss: 0.0045 - val_loss: 0.0109
Epoch 6/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 48s 3s/step - loss: 0.0041 - val_loss: 0.0097
Epoch 7/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 45s 2s/step - loss: 0.0031 - val_loss: 0.0085
Epoch 8/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 41s 2s/step - loss: 0.0027 - val_loss: 0.0082
Epoch 9/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 44s 2s/step - loss: 0.0020 - val_loss: 0.0077
Epoch 10/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 45s 3s/step - loss: 0.0015 - val_loss: 0.0067
Epoch 11/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 42s 2s/step - loss: 0.0014 - val_loss: 0.0059
Epoch 12/180
18/18 ━━━━━━━━━━━━━━━━━━━━ 44s 2s/step - loss: 0.

Zapisujemy model w rozszerzeniu .keras. #TODO opisac co to znaczy

In [32]:
model.save('./object_detection.keras')

# Make Predictions
W tej sekcji będziemy sprawdzać działanie naszego algorytmu. Na początek ładujemy model.

In [13]:
model = tf.keras.models.load_model('./object_detection.keras')
print('Model loaded Sucessfully')

Model loaded Sucessfully


C:\Users\macie\anaconda3\envs\tf_cpu\Lib\site-packages\keras\src\saving\saving_lib.py:396: UserWarning:

Skipping variable loading for optimizer 'rmsprop', because it has 496 variables whereas the saved optimizer has 990 variables. 



Aby sprawdzić działanie algorytmu korzystamy z testowego zdjęcia TEST.jpeg.

In [14]:
path = 'kaggle_dataset001/TEST/TEST.jpeg'
image = load_img(path) # PIL object
image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
image1 = load_img(path,target_size=(224,224))
image_arr_224 = img_to_array(image1)/255.0  # Convert into array and get the normalized output

# Size of the orginal image
h,w,d = image.shape
print('Height of the image =',h)
print('Width of the image =',w)

Height of the image = 729
Width of the image = 901


wyświetlamy zdjęcie

In [15]:
fig = px.imshow(image)
fig.update_layout(width=700, height=500,  margin=dict(l=10, r=10, b=10, t=10), xaxis_title='TEST Image')
fig.show()

sprawdzamy rozmiar zdjęcia.

In [16]:
image_arr_224.shape

(224, 224, 3)

aby przekazać zdjęcie do modelu musimy dodać czwartą wartość, która wskazuje ilość zdjęć do predykcji.

In [17]:
test_arr = image_arr_224.reshape(1,224,224,3)
test_arr.shape

(1, 224, 224, 3)

Używamy modelu aby uzyskać znormalizowane współrzędne.

In [18]:
coords = model.predict(test_arr)
coords

1/1 ━━━━━━━━━━━━━━━━━━━━ 6s 6s/step


array([[0.36328283, 0.65876925, 0.6491009 , 0.74050474]], dtype=float32)

Po denormalizacji otrzymujemy współrzędne **Bounding Box'a**

In [19]:
denorm = np.array([w,w,h,h])
coords = coords * denorm
coords

array([[327.3178294 , 593.55109417, 473.19455588, 539.82795668]])

In [20]:
coords = coords.astype(np.int32)
coords

array([[327, 593, 473, 539]])

In [21]:
# Draw bounding on top the image
xmin, xmax,ymin,ymax = coords[0]
pt1 =(xmin,ymin)
pt2 =(xmax,ymax)
print(pt1, pt2)

(327, 473) (593, 539)


In [22]:
cv2.rectangle(image,pt1,pt2,(0,255,0),3)
fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10))

# Creating pipeline
Definiujemy funkcję, która połączy wszystkie poprzednie etapy. Po podaniu ścieżki do pliku zostaną nam zwrócone współrzędne **Bounding box'a**

In [23]:
def object_detection(path):
    
    # Read image
    image = load_img(path) # PIL object
    image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
    image1 = load_img(path,target_size=(224,224))
    
    # Data preprocessing
    image_arr_224 = img_to_array(image1)/255.0 # Convert to array & normalized
    h,w,d = image.shape
    test_arr = image_arr_224.reshape(1,224,224,3)
    
    # Make predictions
    coords = model.predict(test_arr)
    
    # Denormalize the values
    denorm = np.array([w,w,h,h])
    coords = coords * denorm
    coords = coords.astype(np.int32)
    
    # Draw bounding on top the image
    xmin, xmax,ymin,ymax = coords[0]
    pt1 =(xmin,ymin)
    pt2 =(xmax,ymax)
    print(pt1, pt2)
    cv2.rectangle(image,pt1,pt2,(0,255,0),3)
    return image, coords



In [24]:
path = 'kaggle_dataset001/TEST/TEST.jpeg'
image, cods = object_detection(path)

fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='TEST Image')

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 144ms/step
(327, 473) (593, 539)


### Check pytesseract
sprawdzamy poprawność odczytu tekstu z obrazu

In [3]:
img = cv2.imread("testocr.png")
text = pt.image_to_string(img)
print(text)

This is a lot of 12 point text to test the
ocr code and see if it works on all types
of file format.

The quick brown dog jumped over the
lazy fox. The quick brown dog jumped
over the lazy fox. The quick brown dog
jumped over the lazy fox. The quick
brown dog jumped over the lazy fox.


In [28]:
img = np.array(load_img(path))
xmin ,xmax,ymin,ymax = cods[0]
roi = img[ymin:ymax,xmin:xmax]
fig = px.imshow(roi)
fig.update_layout(width=350, height=250, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='ROI Image')

In [29]:
# extract text from image
text = pt.image_to_string(roi)
print(text)

KL 51 K 4999


wnioski:

ref:
https://www.kaggle.com/code/aslanahmedov/automatic-number-plate-recognition 